---

# S01E02 : Le système d'importation - L'instruction import

Cyril Desjouy

---

Le fonctionnement de l'instruction `import` est très complexe. Le but ici n'est pas d'étudier précisément son fonctionnement, mais seulement d'éclaircir certains points importants pour l'utilisateur.

## 1. Recherche de modules

Quand vous utilisez l'instruction `import`, l'interpréteur Python utilise la fonction spéciale `__import__`.
Ecrire `import os` est un raccourci vers l'instruction `os = __import__('os')`! Importer un module, c’est créer un objet de type module qui est simplement référencé par un ***identifieur*** (un nom, une variable).

Lors de l'exécution de l'instruction `import module`, l'interpréteur Python cherche si `module` a déjà été importé. Si c'est le cas, il retourne le module qu'il a en cache (voir section suivante). Si ce n'est pas le cas, il cherche dans une liste d'emplacement. Cette recherche se fait dans l'ordre suivant:

* dans la bibliothèque standard,
* dans le répertoire courant (celui où le script est exécuté),
* dans le `PYTHONPATH` (liste de répertoires),
* dans la liste de répertoire par défaut (liste configuré au moment de l'installation de Python).

Si l'interpréteur ne trouve le nom `module` dans aucun des emplacements cités ci-dessus, il lève l'exception `ImportError`. La liste des répertoires dans lesquels l'interpréteur cherche les modules/packages est accessible grâce à `sys.path`:
```python
>> import sys
>> sys.path
```

Il est tout à fait possible d'ajouter des répertoires à cette liste:
```python
>> import sys
>> sys.path.append(r'/home/cdesjouy/libs/')
>> import my_module_from_my_libs
```

Il est important de noter que la modification de `sys.path` **n'est pas permanente**. Elle s'étend jusqu'à ce que l'interpréteur dans lequel la modification a été faite termine son exécution. Pour ajouter de manière permanente un répertoire dans la liste des répertoires dans laquelle Python cherche les modules, il faut agir sur la variable d'environnement `PYTHONPATH`. Sous Linux ou mac, il suffit d'ajouter ce type de ligne dans votre `.bashrc`:

```
export PYTHONPATH=$PYTHONPATH:/home/cdesjouy/libs/
```

>**Note:** *Sous windows, il semble que le fichier concerné soit `autoexec.bat`. Conférer:*
* [stackoverflow - add to the PYTHONPATH in windows](https://stackoverflow.com/questions/3701646/how-to-add-to-the-pythonpath-in-windows-so-it-finds-my-modules-packages)
* [Python.org - windows](https://docs.python.org/3.8/using/windows.html)

## 2. Recharger un module

Comme précisé à la section précédente, l'instruction `import module` cherche tout d'abord si `module` a déjà été importé. Si c'est le cas, l'interpréteur Python utilise le module qu'il a en cache (en mémoire) au lieu de le chercher à nouveau. Cela permet d'optimiser l'exécution de codes où le même module pourrait être importé plusieurs fois. Il est cependant possible de forcer le rechargement d'un module en utilisant la fonction `reload` fournie par le module standard `importlib`:

```python
>> import importlib
>> importlib.reload(module)
```

## 3. Les imports absolus et relatifs

Considérons l'arborescence de la figure 1.

```
                                 project
                                    │
                                    └── package
                                        │ 
                                        ├── module1.py
                                        │
                                        ├── module2.py
                                        │
                                        └── subpackage
                                                │
                                                └── module3.py
  
                                      Fig. 1: A project
```

Python propose deux types d'importation:

* **l'importation absolue** spécifie la ressource à importer en utilisant son chemin complet à partir du dossier racine du projet:

```python
import package.module1
import package.subpackage.module3
```

* **l'importation relative** spécifie la ressource à importer par rapport à l'emplacement actuel, c'est-à-dire l'emplacement où se trouve le `import`:

```python
# instructions in file package/module1.py
from .module2 import something
from .subpackage.module3 import something
```

Les imports relatifs peuvent être difficiles à interpréter. Ils n'est pas si évident de savoir où se trouvent les ressources importées. Dans de gros projets où la structure des répertoires est susceptible de changer, les imports relatifs peuvent devenir un véritable casse-tête. De manière générale les imports absolus sont préférés car il restent simples et clairs et la localisation des ressources importées est explicite. 

## 4. Note sur l'attribut `__all__`

Considérons l'arborescence de la figure 1. Lorsque l'instruction suivante est exécutée, on pourrait s'attendre à ce que l'interpréteur Python importe tous les modules contenus dans le package:
```python
>> from package import *
>> dir()
```
Ce n'est pas le cas. La liste retournée par la fonction `dir` ne contient ni `module1`, ni `module2`, ce qui signifie qu'il n'ont pas été importé dans notre ***namespace***. En fait, lorsque l'interpréteur Python rencontre un `import` global (`*`), il cherche tout d'abord si le fichier `__init__.py` (s'il existe) contient la variable spéciale `__all__`. Cette variable peut contenir une liste de noms de ressources (chaînes de caractères). Par exemple:
```python
__all__ = ['module1', 'module2']        ]
```
L'interpréteur agit alors en fonction:
* si `__all__` est défini, `from package import *` importe les **modules listés** dans `__all__`,
* si `__all__` n'est pas défini, `from package import *` n'importe **rien**.

La variable `__all__` peut également être définie au niveau d'un module. Dans ce cas:

* si `__all__` est défini, `from module import *` importe **uniquement les objets de cette liste**,
* si `__all__` n'est pas définie, `from module import *` importe **tous les objets contenus dans le module**.

## Bibliographie

* [Python.org - Modules](https://docs.python.org/3.8/tutorial/modules.html)
* [Python.org - Import](https://docs.python.org/3.8/reference/import.html)
* [Real Python - Modules & Packages](https://realpython.com/python-modules-packages/)
* [Real Python - Absolute vs. relative impors](https://realpython.com/absolute-vs-relative-python-imports/)